<a href="https://colab.research.google.com/github/doronin99/RecoServiceTemplate/blob/task5/notebooks/autoencoder.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Dependencies installing

In [ ]:
!pip -q install dill

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 115.3/115.3 kB 2.4 MB/s eta 0:00:00


In [ ]:
import dill
import math

import numpy as np
import os
import pandas as pd

from IPython.display import display, clear_output

from scipy.sparse import csr_matrix
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

import torch
from torch import nn
from torch.nn import functional as F
from torch.utils.data import Dataset, DataLoader

from tqdm.notebook import tqdm


## Data loading

In [ ]:
!wget -q https://github.com/irsafilo/KION_DATASET/raw/f69775be31fa5779907cf0a92ddedb70037fb5ae/data_original.zip -O data_original.zip
!unzip -o data_original.zip
!rm data_original.zip

Archive:  data_original.zip
   creating: data_original/
  inflating: data_original/interactions.csv  
  inflating: __MACOSX/data_original/._interactions.csv  
  inflating: data_original/users.csv  
  inflating: __MACOSX/data_original/._users.csv  
  inflating: data_original/items.csv  
  inflating: __MACOSX/data_original/._items.csv  


In [ ]:
interactions_df = pd.read_csv('data_original/interactions.csv')
users_df = pd.read_csv('data_original/users.csv')
items_df = pd.read_csv('data_original/items.csv')

In [ ]:
# Filter interactions_df to include only rows where 'last_watch_dt' is before April 1, 2021.
interactions_df = interactions_df[interactions_df['last_watch_dt'] < '2021-04-01']

# Count the number of interactions for each unique pair of 'user_id' and 'item_id',
# then count the number of unique users with at least 5 interactions
users_interactions_count_df = interactions_df.groupby(['user_id', 'item_id']).size().groupby('user_id').size()
users_with_enough_interactions_df = users_interactions_count_df[users_interactions_count_df >= 5].reset_index()[['user_id']]

print('# of interactions: %d' % len(interactions_df))

# Merge interactions_df with users_with_enough_interactions_df based on 'user_id' to
# include only interactions from users with at least 5 interactions
interactions_from_selected_users_df = interactions_df.merge(users_with_enough_interactions_df,
               how='right',
               left_on='user_id',
               right_on='user_id')

print('# of interactions from users with at least 5 interactions: %d' % len(interactions_from_selected_users_df))

# of interactions: 263874
# of interactions from users with at least 5 interactions: 142670


In [ ]:
# Define a function to apply a logarithmic transformation to user preferences
def smooth_user_preference(x):
    return math.log(1 + x, 2)

# Group interactions_from_selected_users_df by 'user_id' and 'item_id', summing up the 'watched_pct',
# then apply the smooth_user_preference function and reset the index
interactions_full_df = interactions_from_selected_users_df \
                    .groupby(['user_id', 'item_id'])['watched_pct'].sum() \
                    .apply(smooth_user_preference).reset_index()

print('# of unique user/item interactions: %d' % len(interactions_full_df))

interactions_full_df.head(10)

# of unique user/item interactions: 142670


user_id  item_id  watched_pct
0       21      849     6.375039
1       21     4345     6.658211
2       21    10283     6.658211
3       21    12261     6.658211
4       21    15997     6.658211
5       32      952     6.044394
6       32     4382     4.954196
7       32     4807     6.658211
8       32    10436     6.658211
9       32    12132     6.658211

## Train/Test splitting

In [ ]:
# Split interactions_full_df into training and testing sets, maintaining stratification based on 'user_id'
interactions_train_df, interactions_test_df = train_test_split(interactions_full_df,
                                   stratify=interactions_full_df['user_id'],
                                   test_size=0.20,
                                   random_state=42)

print('# interactions on Train set: %d' % len(interactions_train_df))
print('# interactions on Test set: %d' % len(interactions_test_df))

# interactions on Train set: 114136
# interactions on Test set: 28534


In [ ]:
# Indexing by personId to speed up the searches during evaluation
interactions_full_indexed_df = interactions_full_df.set_index('user_id')
interactions_train_indexed_df = interactions_train_df.set_index('user_id')
interactions_test_indexed_df = interactions_test_df.set_index('user_id')

In [ ]:
# Define a function to retrieve items interacted by a given person_id from interactions_df
def get_items_interacted(person_id, interactions_df):
    interacted_items = interactions_df.loc[person_id]['item_id']
    return set(interacted_items if type(interacted_items) == pd.Series else [interacted_items])

## ModelEvaluator class

In [ ]:
# Top-N accuracy metrics consts
EVAL_RANDOM_SAMPLE_NON_INTERACTED_ITEMS = 100

class ModelEvaluator:


    def get_not_interacted_items_sample(self, person_id, sample_size, seed=42):
        interacted_items = get_items_interacted(person_id, interactions_full_indexed_df)
        all_items = set(articles_df['item_id'])
        non_interacted_items = all_items - interacted_items

        random.seed(seed)
        non_interacted_items_sample = random.sample(non_interacted_items, sample_size)
        return set(non_interacted_items_sample)

    def _verify_hit_top_n(self, item_id, recommended_items, topn):
            try:
                index = next(i for i, c in enumerate(recommended_items) if c == item_id)
            except:
                index = -1
            hit = int(index in range(0, topn))
            return hit, index

    def evaluate_model_for_user(self, model, person_id):
        #Getting the items in test set
        interacted_values_testset = interactions_test_indexed_df.loc[person_id]
        if type(interacted_values_testset['item_id']) == pd.Series:
            person_interacted_items_testset = set(interacted_values_testset['item_id'])
        else:
            person_interacted_items_testset = set([int(interacted_values_testset['item_id'])])
        interacted_items_count_testset = len(person_interacted_items_testset)

        #Getting a ranked recommendation list from a model for a given user
        person_recs_df = model.recommend_items(person_id,
                                               items_to_ignore=get_items_interacted(person_id,
                                                                                    interactions_train_indexed_df),
                                               topn=10000000000)

        hits_at_5_count = 0
        hits_at_10_count = 0
        #For each item the user has interacted in test set
        for item_id in person_interacted_items_testset:
            #Getting a random sample (100) items the user has not interacted
            #(to represent items that are assumed to be no relevant to the user)
            non_interacted_items_sample = self.get_not_interacted_items_sample(person_id,
                                                                          sample_size=EVAL_RANDOM_SAMPLE_NON_INTERACTED_ITEMS,
                                                                          seed=item_id%(2**32))

            #Combining the current interacted item with the 100 random items
            items_to_filter_recs = non_interacted_items_sample.union(set([item_id]))

            #Filtering only recommendations that are either the interacted item or from a random sample of 100 non-interacted items
            valid_recs_df = person_recs_df[person_recs_df['item_id'].isin(items_to_filter_recs)]
            valid_recs = valid_recs_df['item_id'].values
            #Verifying if the current interacted item is among the Top-N recommended items
            hit_at_5, index_at_5 = self._verify_hit_top_n(item_id, valid_recs, 5)
            hits_at_5_count += hit_at_5
            hit_at_10, index_at_10 = self._verify_hit_top_n(item_id, valid_recs, 10)
            hits_at_10_count += hit_at_10

        #Recall is the rate of the interacted items that are ranked among the Top-N recommended items,
        #when mixed with a set of non-relevant items
        recall_at_5 = hits_at_5_count / float(interacted_items_count_testset)
        recall_at_10 = hits_at_10_count / float(interacted_items_count_testset)

        person_metrics = {'hits@5_count':hits_at_5_count,
                          'hits@10_count':hits_at_10_count,
                          'interacted_count': interacted_items_count_testset,
                          'recall@5': recall_at_5,
                          'recall@10': recall_at_10}
        return person_metrics

    def evaluate_model(self, model):
        #print('Running evaluation for users')
        people_metrics = []
        for idx, person_id in enumerate(tqdm(list(interactions_test_indexed_df.index.unique().values))):
            #if idx % 100 == 0 and idx > 0:
            #    print('%d users processed' % idx)
            person_metrics = self.evaluate_model_for_user(model, person_id)
            person_metrics['user_id'] = person_id
            people_metrics.append(person_metrics)
        print('%d users processed' % idx)

        detailed_results_df = pd.DataFrame(people_metrics) \
                            .sort_values('interacted_count', ascending=False)

        global_recall_at_5 = detailed_results_df['hits@5_count'].sum() / float(detailed_results_df['interacted_count'].sum())
        global_recall_at_10 = detailed_results_df['hits@10_count'].sum() / float(detailed_results_df['interacted_count'].sum())

        global_metrics = {'modelName': model.get_model_name(),
                          'recall@5': global_recall_at_5,
                          'recall@10': global_recall_at_10}
        return global_metrics, detailed_results_df

In [ ]:
model_evaluator = ModelEvaluator()

## Main

In [ ]:
# Constants
SEED = 42 # random seed for reproducibility
LR = 1e-3 # learning rate, controls the speed of the training
WEIGHT_DECAY = 0.01 # lambda for L2 reg. ()
NUM_EPOCHS = 200 # num training epochs (how many times each instance will be processed)
GAMMA = 0.9995 # learning rate scheduler parameter
BATCH_SIZE = 3000 # training batch size
EVAL_BATCH_SIZE = 3000 # evaluation batch size.
DEVICE = 'cuda' #'cuda' # device to make the calculations on

In [ ]:
# Concatenate interactions_train_df and interactions_test_indexed_df.reset_index() to create total_df
total_df = interactions_train_df.append(interactions_test_indexed_df.reset_index())

# Encode 'user_id' and 'item_id' using factorization and store the mapping in users_keys and items_keys
total_df['user_id'], users_keys = total_df.user_id.factorize()
total_df['item_id'], items_keys = total_df.item_id.factorize()

# Separate the encoded data into training (train_encoded) and testing (test_encoded) sets
train_encoded = total_df.iloc[:len(interactions_train_df)].values
test_encoded = total_df.iloc[len(interactions_train_df):].values

<ipython-input-13-e8ddcec99f63>:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_df = interactions_train_df.append(interactions_test_indexed_df.reset_index())


In [ ]:
# Define the shape of the sparse matrix based on the maximum 'user_id' and 'item_id' values
shape = [int(total_df['user_id'].max() + 1), int(total_df['item_id'].max() + 1)]

# Create a sparse matricies
X_train = csr_matrix((train_encoded[:, 2], (train_encoded[:, 0], train_encoded[:, 1])), shape=shape).toarray()
X_test = csr_matrix((test_encoded[:, 2], (test_encoded[:, 0], test_encoded[:, 1])), shape=shape).toarray()

In [ ]:
# Initialize the DataObject, which must return an element (features vector x and target value y)
# for a given idx. This class must also have a length atribute
class UserOrientedDataset(Dataset):
    def __init__(self, X):
        super().__init__() # to initialize the parent class
        self.X = X.astype(np.float32)
        self.len = len(X)

    def __len__(self): # We use __func__ for implementing in-built python functions
        return self.len

    def __getitem__(self, index):
        return self.X[index]

In [ ]:
# Initialize DataLoaders - objects, which sample instances from DataObject-s
train_dl = DataLoader(
    UserOrientedDataset(X_train),
    batch_size = BATCH_SIZE,
    shuffle = True
)

test_dl = DataLoader(
    UserOrientedDataset(X_test),
    batch_size = EVAL_BATCH_SIZE,
    shuffle = False
)

dls = {'train': train_dl, 'test': test_dl}

In [ ]:
class ModifiedModel(nn.Module):
    def __init__(self, in_and_out_features=8287, hidden_sizes=[500, 300, 100], dropout_prob=0.5):
        super(ModifiedModel, self).__init__()
        self.in_and_out_features = in_and_out_features
        self.hidden_sizes = hidden_sizes
        self.dropout_prob = dropout_prob

        layers = []
        prev_size = in_and_out_features

        for hidden_size in hidden_sizes:
            layers.append(nn.Linear(prev_size, hidden_size))
            layers.append(nn.ReLU())
            layers.append(nn.BatchNorm1d(hidden_size))
            layers.append(nn.Dropout(p=dropout_prob))
            prev_size = hidden_size

        layers.append(nn.Linear(hidden_sizes[-1], in_and_out_features))

        self.sequential = nn.Sequential(*layers)

    def forward(self, x):
        x = self.sequential(x)
        return x

In [ ]:
# Define a function to calculate the Root Mean Squared Error (RMSE) for sparse matrices
def rmse_for_sparse(x_pred, x_true):
    mask = (x_true > 0)
    sq_diff = (x_pred * mask - x_true) ** 2
    mse = sq_diff.sum() / mask.sum()
    return mse ** 0.5

In [ ]:
torch.manual_seed(SEED)

modified_model = ModifiedModel()

optimizer = torch.optim.AdamW(modified_model.parameters(), lr=LR, weight_decay=WEIGHT_DECAY)
scheduler = torch.optim.lr_scheduler.ExponentialLR(optimizer, gamma=GAMMA)

metrics_dict = {
    "Epoch": [],
    "Train RMSE": [],
    "Test RMSE": [],
}

for epoch in range(NUM_EPOCHS):
    metrics_dict["Epoch"].append(epoch)
    for stage in ['train', 'test']:
        with torch.set_grad_enabled(stage == 'train'):
            if stage == 'train':
                modified_model.train()
            else:
                modified_model.eval()

            loss_at_stage = 0

            for batch in tqdm(dls[stage], desc=f'{stage.title()} Epoch {epoch + 1}/{NUM_EPOCHS}'):
                x_pred = modified_model(batch)
                loss = rmse_for_sparse(x_pred, batch)
                if stage == "train":
                    loss.backward()
                    optimizer.step()
                    scheduler.step()
                    optimizer.zero_grad()
                loss_at_stage += loss.item() * len(batch)
            rmse_at_stage = (loss_at_stage / len(dls[stage].dataset)) ** (1/2)
            metrics_dict[f"{stage.title()} RMSE"].append(rmse_at_stage)

    if (epoch == NUM_EPOCHS - 1) or epoch % 10 == 9:
        clear_output(wait=True)
        display(pd.DataFrame(metrics_dict))

Epoch  Train RMSE  Test RMSE
0        0    2.331792   2.332321
1        1    2.269858   2.328166
2        2    2.223258   2.314025
3        3    2.189824   2.287003
4        4    2.156387   2.249469
..     ...         ...        ...
195    195    1.131764   1.288431
196    196    1.135306   1.290121
197    197    1.130808   1.295014
198    198    1.135216   1.296818
199    199    1.129576   1.298894

[200 rows x 3 columns]

In [ ]:
# Use torch.no_grad() to disable gradient tracking during prediction
with torch.no_grad():
    # Pass the testing data X_test through the more_complex_model to get predictions
    X_pred = modified_model(torch.Tensor(X_test))

X_pred

tensor([[ 4.4537,  5.4423,  2.1971,  ..., -0.3151, -0.4209,  0.0325],
        [ 0.2235, -0.2846, -0.5021,  ...,  0.0726, -0.2639, -0.2892],
        [ 2.1069,  1.7670,  3.0536,  ..., -0.0586, -0.4127,  0.6119],
        ...,
        [-0.1082, -0.7450,  0.2494,  ...,  0.1019, -0.2107, -0.2765],
        [ 1.8451,  0.2363,  1.7619,  ..., -0.0160, -0.2068,  0.6421],
        [ 2.0922,  1.8690,  1.6863,  ..., -0.2225,  0.6030,  0.6827]])

In [ ]:
class AERecommender:

    MODEL_NAME = 'Autoencoder'

    def __init__(self, X_preds, X_train_and_val, X_test):

        self.X_preds = X_preds.cpu().detach().numpy()
        self.X_train_and_val = X_train_and_val
        self.X_test = X_test

    def get_model_name(self):
        return self.MODEL_NAME

    def recommend_items(self, user_id, topn=10):
        user_preds = self.X_preds[user_id]
        items_idx = np.argsort(-user_preds)[:topn]

        # Recommend the highest predicted rating movies that the user hasn't seen yet.
        return items_idx

    def evaluate(self, size=100):
        X_total = self.X_train_and_val + self.X_test

        true_5 = []
        true_10 = []

        for user_id in range(len(self.X_test)):
            non_zero = np.argwhere(self.X_test[user_id] > 0).ravel()
            all_nonzero = np.argwhere(X_total[user_id] > 0).ravel()
            select_from = np.setdiff1d(np.arange(X_total.shape[1]), all_nonzero)

            for non_zero_idx in non_zero:
                preds = self.recommend_items(user_id, topn=10)
                true_5.append(non_zero_idx in preds[:5])
                true_10.append(non_zero_idx in preds)

        return {"recall@5": np.mean(true_5), "recall@10": np.mean(true_10)}

In [ ]:
ae_recommender_model = AERecommender(X_pred, X_train, X_train)

In [ ]:
ae_global_metrics = ae_recommender_model.evaluate()
ae_global_metrics

{'recall@5': 0.004612519137566189, 'recall@10': 0.010395233405170312}

In [ ]:
ae_recommender_model.recommend_items(11)

array([  47, 1727,  686,  843, 1360, 1838,  512, 4096, 1306,  266])

## Model saving

In [ ]:
# Save the model to a file using dill
with open('ae_recommender_model.dill', 'wb') as f:
    dill.dump(ae_recommender_model, f)